In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tensorflow as tf
import re
# from google_trans_new import google_translator
# from translate import Translator
# from googletrans import Translator
from itertools import chain
import glob
import seaborn as sns
import matplotlib.font_manager as font_manager
import seaborn as sns
import matplotlib as mpl
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import scale 
from sklearn import model_selection
from sklearn.model_selection import RepeatedKFold
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_regression
from sklearn.neural_network import MLPRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.ensemble import RandomForestRegressor, AdaBoostRegressor
from sklearn.linear_model import SGDRegressor
from xgboost import XGBRegressor
from sklearn.preprocessing import StandardScaler
from lightgbm import LGBMRegressor
from collections import Counter
from pandas import read_csv
from datetime import datetime
from sklearn.metrics import mean_absolute_percentage_error
from statsmodels.tsa.stattools import adfuller
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.arima_model import ARIMA
from statsmodels.tsa.statespace.sarimax import SARIMAX
from pandas.plotting import register_matplotlib_converters
import warnings
import itertools
import math
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import KFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.models import load_model


# translator = google_translator()
# translator = Translator(to_lang='ch')
warnings.filterwarnings('ignore')

sns.set_theme()
mpl.matplotlib_fname()
font_dirs = ['D:\\Software\\Anaconda\\Lib\\site-packages\\matplotlib\\mpl-data\\fonts\\ttf' ]
font_files = font_manager.findSystemFonts(fontpaths=font_dirs)
for font_file in font_files:
    font_manager.fontManager.addfont(font_file)
mpl.font_manager._rebuild()
result = font_manager.findfont("Rounded Mplus 1c")
print(result)
mpl.rc('font', family='Rounded Mplus 1c')

In [ ]:
df = pd.read_csv('Kaiho_merged_data.csv')
df.columns

In [113]:
df['date_time'] = df['Năm bán hàng_売上年'].astype(str) +'-'+df['Tháng bán hàng_売上月'].astype(str)+'-'+df['Ngày bán hàng_売上日'].astype(str)
df['date_time']  = pd.to_datetime(df['date_time'],format="%Y-%m-%d")

In [114]:
names = ["Gradient_Boosting", "Decision_Tree", "Extra_Trees", "Random_Forest","XGBoost"]
models = [
    GradientBoostingRegressor(),
    DecisionTreeRegressor(max_depth=5),
    ExtraTreesRegressor(),
    RandomForestRegressor(),
    XGBRegressor()]

In [115]:
Q1 = np.percentile(df['Thành tích bán ra_販売実績'], 25,
                   interpolation = 'midpoint')
 
Q3 = np.percentile(df['Thành tích bán ra_販売実績'], 75,
                   interpolation = 'midpoint')
IQR = Q3 - Q1

df_no_outlier = df[(df['Thành tích bán ra_販売実績'] >= (Q1-1.5*IQR)) & (df['Thành tích bán ra_販売実績'] <= (Q3+1.5*IQR))]
df_no_outlier


Vị trí_ロケーション  Ngày sản xuất_生産日  Tháng sản xuất_生産月  Năm sản xuất_生産年  \
0            会宝産業本社                 17                  11              2015   
1            会宝産業本社                  3                   2              2015   
2            会宝産業本社                  3                   2              2015   
3            会宝産業本社                  5                   2              2015   
4            会宝産業本社                 25                   2              2015   
...             ...                ...                 ...               ...   
20423        会宝産業本社                 10                   9              2012   
20424        会宝産業本社                 27                   8              2012   
20425        会宝産業本社                 23                   8              2012   
20426        会宝産業本社                  6                  11              2012   
20427        会宝産業本社                  4                  12              2012   

      Nv sản xuất_生産担当者 Số nhập kho_入庫番号    Nguồn nhập hàng_仕入先  \
0                  山下大輝   '0000000302676                  西田 敏勝   
1                  中嶋　修   '0000000303771                ｴｻﾞｼ自動車   
2                  楊　志毅   '0000000303771                ｴｻﾞｼ自動車   
3                  西川航平   '0000000314958                   ＪＵ石川   
4                  中里太明   '0000000319165  会宝パーツサービス㈲福井店　アップガレージ   
...                 ...              ...                    ...   
20423              中谷祐騎   '0000000297532                石川トヨタ本社   
20424              坂尻僚平   '0000000297920                   ＪＵ石川   
20425              菊池忠義   '0000000298205                  西村 信與   
20426              坂尻僚平   '0000000300843                  エステート   
20427              菊池忠義   '0000000303083           石川県消防学校運営協議会   

      Mã loại phụ tùng_商品コード Tên phụ tùng_商品名 Số nhập kho(phụ tùng)_入庫番号 (部品)  \
0                    '110010       ノーズカット（個別）                  '0000007988203   
1                    '100000             エンジン                  '0000007739581   
2                    '110010       ノーズカット（個別）                  '0000007712751   
3                    '110010       ノーズカット（個別）                  '0000007732276   
4                    '110010       ノーズカット（個別）                  '0000007742703   
...                      ...              ...                             ...   
20423                '110010       ノーズカット（個別）                  '0000007022141   
20424                '140092       Ｆアクスル（生/Ｄ）                  '0000007052516   
20425                '140092       Ｆアクスル（生/Ｄ）                  '0000005002723   
20426                '140153       Ｒアクスル（生/Ｄ）                  '0000007076751   
20427                '140153       Ｒアクスル（生/Ｄ）                  '0000007131858   

       ... Mã nhà cung cấp_仕入先コード Số body_車体番号 CONTAINER_CONTAINER  \
0      ...               990010.0     '1001019                 NaN   
1      ...               990000.0     '6062039                40HC   
2      ...               990000.0     '6062039                40HC   
3      ...               319800.0     '2010272                40HC   
4      ...               208750.0      '072307                40HC   
...    ...                    ...          ...                 ...   
20423  ...               111300.0     '0113274                  20   
20424  ...               319800.0     '0020874                  20   
20425  ...               990010.0      '101069                  20   
20426  ...               135300.0     '0010109                  20   
20427  ...               110700.0     '1000906                  20   

             Tên khách hàng_売上先名  Phân loại mang đến/đón_持込・引取区分  \
0         一番オート   OOO "LIGHT VL"                             NaN   
1                木戸クンク・ジャイブ（ＥＫ３）                             NaN   
2                木戸クンク・ジャイブ（ＥＫ３）                             NaN   
3      ㈱パシフィック・トレーディング・インターナショナル                             NaN   
4      ㈱パシフィック・トレーディング・インターナショナル                             NaN   
...               

In [655]:
df_copy = df.copy()
# df_copy = df_no_outlier.copy()

# target = df_copy['Thành tích bán ra_販売実績']

In [656]:
df_mean = df.groupby(['Tên phụ tùng_商品名','Model xe_車輌型式','Engine model_エンジン型式'])['Thành tích bán ra_販売実績'].mean().reset_index(name='mean_price')
df_mean

Tên phụ tùng_商品名 Model xe_車輌型式 Engine model_エンジン型式    mean_price
0                エンジン         1C8F4          CHRYSLER-T  30000.000000
1                エンジン       1GCDL19             CHEV-4G  30000.000000
2                エンジン      1GNEL19W             CHEV-4G  35000.000000
3                エンジン           A32              VQ20DE  36000.000000
4                エンジン           A33              VQ20DE  39117.647059
...               ...           ...                 ...           ...
3387       Ｒアクスル（生/Ｄ）      YV194586          VOLVO-B230  10000.000000
3388       Ｒアクスル（生/Ｄ）         YXS11               3Y-PE   5000.000000
3389       Ｒアクスル（生/Ｄ）          Z22A                4A90   9000.000000
3390       Ｒアクスル（生/Ｄ）          Z26A                4G19   8000.000000
3391       Ｒアクスル（生/Ｄ）         ZGM15              2ZR-FE   2500.000000

[3392 rows x 4 columns]

In [657]:
df_merge_mean = pd.merge(df_copy,df_mean,on=['Tên phụ tùng_商品名','Model xe_車輌型式','Engine model_エンジン型式'],how='left')
df_merge_mean

Vị trí_ロケーション  Ngày sản xuất_生産日  Tháng sản xuất_生産月  Năm sản xuất_生産年  \
0            会宝産業本社                 17                  11              2015   
1            会宝産業本社                  3                   2              2015   
2            会宝産業本社                  3                   2              2015   
3            会宝産業本社                  5                   2              2015   
4            会宝産業本社                 25                   2              2015   
...             ...                ...                 ...               ...   
20423        会宝産業本社                 10                   9              2012   
20424        会宝産業本社                 27                   8              2012   
20425        会宝産業本社                 23                   8              2012   
20426        会宝産業本社                  6                  11              2012   
20427        会宝産業本社                  4                  12              2012   

      Nv sản xuất_生産担当者 Số nhập kho_入庫番号    Nguồn nhập hàng_仕入先  \
0                  山下大輝   '0000000302676                  西田 敏勝   
1                  中嶋　修   '0000000303771                ｴｻﾞｼ自動車   
2                  楊　志毅   '0000000303771                ｴｻﾞｼ自動車   
3                  西川航平   '0000000314958                   ＪＵ石川   
4                  中里太明   '0000000319165  会宝パーツサービス㈲福井店　アップガレージ   
...                 ...              ...                    ...   
20423              中谷祐騎   '0000000297532                石川トヨタ本社   
20424              坂尻僚平   '0000000297920                   ＪＵ石川   
20425              菊池忠義   '0000000298205                  西村 信與   
20426              坂尻僚平   '0000000300843                  エステート   
20427              菊池忠義   '0000000303083           石川県消防学校運営協議会   

      Mã loại phụ tùng_商品コード Tên phụ tùng_商品名 Số nhập kho(phụ tùng)_入庫番号 (部品)  \
0                    '110010       ノーズカット（個別）                  '0000007988203   
1                    '100000             エンジン                  '0000007739581   
2                    '110010       ノーズカット（個別）                  '0000007712751   
3                    '110010       ノーズカット（個別）                  '0000007732276   
4                    '110010       ノーズカット（個別）                  '0000007742703   
...                      ...              ...                             ...   
20423                '110010       ノーズカット（個別）                  '0000007022141   
20424                '140092       Ｆアクスル（生/Ｄ）                  '0000007052516   
20425                '140092       Ｆアクスル（生/Ｄ）                  '0000005002723   
20426                '140153       Ｒアクスル（生/Ｄ）                  '0000007076751   
20427                '140153       Ｒアクスル（生/Ｄ）                  '0000007131858   

       ... Số body_車体番号 CONTAINER_CONTAINER        Tên khách hàng_売上先名  \
0      ...     '1001019                 NaN     一番オート   OOO "LIGHT VL"   
1      ...     '6062039                40HC            木戸クンク・ジャイブ（ＥＫ３）   
2      ...     '6062039                40HC            木戸クンク・ジャイブ（ＥＫ３）   
3      ...     '2010272                40HC  ㈱パシフィック・トレーディング・インターナショナル   
4      ...      '072307                40HC  ㈱パシフィック・トレーディング・インターナショナル   
...    ...          ...                 ...                        ...   
20423  ...     '0113274                  20               TTO Co., LTD   
20424  ...     '0020874                  20              FADEEV EVGENY   
20425  ...      '101069                  20              FADEEV EVGENY   
20426  ...     '0010109                  20              FADEEV EVGENY   
20427  ...     '1000906                  20              FADEEV EVGENY   

       Phân loại mang đến/đón_持込・引取区分  Tiền công_工賃  D/G_Ｄ／Ｇ  \
0                                 NaN           0.0        G   
1                                 NaN           0.0        G   
2                                 NaN           0.0        G   
3                                 NaN           0.0        G   
4                                 NaN           0.0       

In [658]:
list_features = ['Tên phụ tùng_商品名',
                 'Model xe_車輌型式',
                 'Engine model_エンジン型式',
                 'Tháng bán hàng_売上月',
                 'Năm bán hàng_売上年',
#                  'Khách hàng_仕向先',
                 'Thành tích bán ra_販売実績',
                  'mean_price']

In [659]:
df_best = df_merge_mean[list_features]
df_best.dropna(inplace = True)

In [660]:
df_best

Tên phụ tùng_商品名 Model xe_車輌型式 Engine model_エンジン型式  Tháng bán hàng_売上月  \
0           ノーズカット（個別）           ES9             LDA-MF5                   3   
1                 エンジン         AT211               7A-FE                   2   
2           ノーズカット（個別）         AT211               7A-FE                   2   
3           ノーズカット（個別）           RN1                D17A                   2   
4           ノーズカット（個別）           A33              VQ20DE                   3   
...                ...           ...                 ...                 ...   
20423       ノーズカット（個別）        NZE121              1NZ-FE                   9   
20424       Ｆアクスル（生/Ｄ）          PD8W              4M40-T                   9   
20425       Ｆアクスル（生/Ｄ）         SK22M                  R2                   9   
20426       Ｒアクスル（生/Ｄ）          CM41                  2C                  11   
20427       Ｒアクスル（生/Ｄ）           V34              4D56-T                  12   

       Năm bán hàng_売上年  Thành tích bán ra_販売実績    mean_price  
0                  2016                 12000.0  12000.000000  
1                  2015                 30000.0  32854.014599  
2                  2015                 10000.0  10070.175439  
3                  2015                 12000.0  10800.000000  
4                  2015                 10000.0  11571.428571  
...                 ...                     ...           ...  
20423              2012                 12000.0  30800.000000  
20424              2012                  3500.0   3500.000000  
20425              2012                  3500.0   3500.000000  
20426              2012                  5000.0   5000.000000  
20427              2012                  5000.0   5000.000000  

[20425 rows x 7 columns]

In [661]:
le_name = LabelEncoder()
le_model = LabelEncoder()
le_engine = LabelEncoder()
le_customer = LabelEncoder()

le_name.fit_transform(df_copy['Tên phụ tùng_商品名'])
le_model.fit_transform(df_copy['Model xe_車輌型式'])
le_engine.fit_transform(df_copy['Engine model_エンジン型式'])
le_customer.fit_transform(df_copy['Khách hàng_仕向先'])

array([65, 94, 94, ..., 23, 23, 23])

In [662]:
le_customer.classes_

array(['A.K.Muyimbwa Auto parts Ltd.ｳｶﾞﾝﾀﾞ  ｱﾝﾄﾞﾘｭｰ', 'AMIN TRADING',
       'ASHOK AUTO WAY', 'ATC ALYANS  ', 'AUTOHELP', 'AUTOPARTS 1279ﾏﾙﾀ',
       'AVTOTAUN+ CO LTD', 'Autoradyga,ltd - IP Demchuk O. A.',
       'Avtopartner', 'BEST MOTORS company',
       'CHOWDHURY TRADING\u3000ﾊﾞﾝｸﾞﾗ ﾁｮｰﾄﾞﾘ', 'CITYZAP',
       'Classic Engines cc', 'Collision Specialist', 'DABAK TRADING ',
       'DAISHIN BOHEKI（大真貿易）', 'DALCOR CO.,LTD', 'DVparts',
       'EASTERN AUTO HOUSE ﾗｼｯﾄﾞ', 'ELIAS CRUZ MONTES',
       'ENGINE WORLD LLC', 'ES PARTS\u3000',
       'Element Parts ﾛｼｱ ｴﾚﾒﾝﾄﾊﾟｰﾂ', 'FADEEV EVGENY',
       'FUSHIMI AUTO PART (旧 KEJOS ）', 'GTMotors ﾛｼｱ GT',
       'HERDEZ CORPORACION S.A.C. ﾍﾟﾙｰ ｴﾙｱﾙﾄﾞ',
       'Hira Enterprises Co Ltd.', 'I.P. POPOV S.V.',
       'IGOR G.REZNIKOV\u3000ﾛｼｱ ｲｸﾞﾘ',
       'IMPORT & EXPORT AZUMI LIMITADA\u3000',
       'IMPORT & EXPORT SEGUNDO GARCIA ESCOBAR E.I.R.L.',
       'IMPORTADORA Y EXPORTADORA DE PRODUCTOS GII LIMITADA',
       'IMPORTADORA Y EXPORTADORA H

In [663]:
categoric_col = []
for col in df_best.columns[df_best.dtypes == 'object']:
        df_best[col].fillna(value='unknown',inplace=True)
        le = LabelEncoder()
        df_best[col] = le.fit_transform(df_best[col].values)
        categorical_col.append(col)

In [664]:
data = df_best.drop(columns=['Thành tích bán ra_販売実績','mean_price'])
target = df_best['Thành tích bán ra_販売実績']

In [665]:
data

Tên phụ tùng_商品名  Model xe_車輌型式  Engine model_エンジン型式  \
0                     1            370                  386   
1                     0             73                  156   
2                     1             73                  156   
3                     1           1069                  234   
4                     1              5                  477   
...                 ...            ...                  ...   
20423                 1            953                   23   
20424                10            982                  132   
20425                10           1151                  426   
20426                11            212                   34   
20427                11           1342                   97   

       Tháng bán hàng_売上月  Năm bán hàng_売上年  
0                       3              2016  
1                       2              2015  
2                       2              2015  
3                       2              2015  
4                       3              2015  
...                   ...               ...  
20423                   9              2012  
20424                   9              2012  
20425                   9              2012  
20426                  11              2012  
20427                  12              2012  

[20425 rows x 5 columns]

In [666]:
X_train, X_test,y_train,y_test = train_test_split(data, target, test_size=0.3, random_state=42)

In [667]:
X_train

Tên phụ tùng_商品名  Model xe_車輌型式  Engine model_エンジン型式  \
14173                 0           1069                  234   
3054                  0            537                    3   
19771                 0            196                  319   
13227                 0           1298                  361   
10622                 0            191                  275   
...                 ...            ...                  ...   
11285                 0            808                  479   
11965                 0           1211                   71   
5391                  8            404                  417   
861                   0            827                   18   
15798                 0            351                  140   

       Tháng bán hàng_売上月  Năm bán hàng_売上年  
14173                   7              2019  
3054                    7              2018  
19771                  10              2012  
13227                  10              2016  
10622                   6              2014  
...                   ...               ...  
11285                   9              2014  
11965                   5              2016  
5391                    5              2017  
861                     6              2015  
15798                  12              2010  

[14297 rows x 5 columns]

In [668]:
X_test

Tên phụ tùng_商品名  Model xe_車輌型式  Engine model_エンジン型式  \
15210                 0            153                  269   
5938                  0           1425                  166   
18139                 0           1139                  265   
19893                 0           1395                  214   
14070                 1           1265                   52   
...                 ...            ...                  ...   
14020                 1             15                   31   
17559                 0            362                  101   
5119                  0            152                  264   
2232                  0            446                  372   
18310                 0           1585                   30   

       Tháng bán hàng_売上月  Năm bán hàng_売上年  
15210                  12              2019  
5938                   10              2017  
18139                   2              2014  
19893                   9              2012  
14070                   5              2019  
...                   ...               ...  
14020                   4              2019  
17559                  10              2013  
5119                    3              2017  
2232                    3              2018  
18310                   2              2012  

[6128 rows x 5 columns]

In [669]:
y_train

14173     55000.0
3054      30000.0
19771     30000.0
13227     25000.0
10622     40000.0
           ...   
11285     30000.0
11965     45000.0
5391     133800.0
861       85000.0
15798     17000.0
Name: Thành tích bán ra_販売実績, Length: 14297, dtype: float64

In [670]:
y_test

15210    40000.0
5938     38000.0
18139    35000.0
19893    42000.0
14070    10000.0
          ...   
14020     9000.0
17559    35000.0
5119     25000.0
2232     20000.0
18310    80000.0
Name: Thành tích bán ra_販売実績, Length: 6128, dtype: float64

# Neural Network Model

In [684]:
NN_model = Sequential()

# The Input Layer :
NN_model.add(Dense(32, kernel_initializer='normal',input_dim = X_train.shape[1], activation='relu'))
# The Hidden Layers :

NN_model.add(Dense(32, kernel_initializer='normal', activation='relu'))

NN_model.add(Dense(64, kernel_initializer='normal', activation='relu'))
NN_model.add(Dense(64, kernel_initializer='normal', activation='relu'))
NN_model.add(Dense(64, kernel_initializer='normal', activation='relu'))

NN_model.add(Dense(128, kernel_initializer='normal', activation='relu'))
NN_model.add(Dense(128, kernel_initializer='normal', activation='relu'))
NN_model.add(Dense(128, kernel_initializer='normal', activation='relu'))

NN_model.add(Dense(256, kernel_initializer='normal',activation='relu'))
NN_model.add(Dense(256, kernel_initializer='normal',activation='relu'))
NN_model.add(Dense(256, kernel_initializer='normal',activation='relu'))

NN_model.add(Dense(512, kernel_initializer='normal',activation='relu'))

# The Output Layer :
NN_model.add(Dense(1, kernel_initializer='normal',activation='linear'))

# Compile the network :
NN_model.compile(loss=tf.keras.losses.MeanAbsolutePercentageError(), optimizer='adam',metrics=[tf.keras.metrics.RootMeanSquaredError(name='rmse'),tf.keras.losses.MeanAbsolutePercentageError(name='mape')])
NN_model.summary()

Model: "sequential_43"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_546 (Dense)            (None, 32)                192       
_________________________________________________________________
dense_547 (Dense)            (None, 32)                1056      
_________________________________________________________________
dense_548 (Dense)            (None, 64)                2112      
_________________________________________________________________
dense_549 (Dense)            (None, 64)                4160      
_________________________________________________________________
dense_550 (Dense)            (None, 64)                4160      
_________________________________________________________________
dense_551 (Dense)            (None, 128)               8320      
_________________________________________________________________
dense_552 (Dense)            (None, 128)             

In [685]:
batch_size = 1024
epochs = 100000

In [686]:
# checkpoint_name = f'best_model_neural_network_del_outlier_{batch_size}.h5' 
# checkpoint_name = f'best_model_neural_network_del_outlier_with_customer_{batch_size}.h5'
# checkpoint_name = f'best_model_neural_network_with_customer_{batch_size}.h5' 
checkpoint_name = f'best_model_neural_network_{batch_size}.h5' 
checkpoint = ModelCheckpoint(filepath= checkpoint_name, monitor='val_mape', verbose = 1, save_best_only = True, mode ='auto')
callbacks_list = [checkpoint]

In [ ]:
NN_model.fit(X_train, y_train, 
             epochs=epochs, 
             batch_size=batch_size, 
             validation_split = 0.2 , 
             callbacks=callbacks_list,
             verbose = 1)

Epoch 1/100000
12/12 [==============================] - 1s 37ms/step - loss: 99.9996 - rmse: 52177.1235 - mape: 99.9995 - val_loss: 99.9853 - val_rmse: 52822.3984 - val_mape: 99.9854

Epoch 00001: val_mape improved from inf to 99.98537, saving model to best_model_neural_network_1024.h5
Epoch 2/100000
12/12 [==============================] - 0s 18ms/step - loss: 99.7412 - rmse: 52296.5415 - mape: 99.7013 - val_loss: 92.2662 - val_rmse: 51652.3438 - val_mape: 92.2975

Epoch 00002: val_mape improved from 99.98537 to 92.29752, saving model to best_model_neural_network_1024.h5
Epoch 3/100000
12/12 [==============================] - 0s 20ms/step - loss: 76.6628 - rmse: 47955.5000 - mape: 76.5408 - val_loss: 61.2076 - val_rmse: 45422.3984 - val_mape: 61.1659

Epoch 00003: val_mape improved from 92.29752 to 61.16594, saving model to best_model_neural_network_1024.h5
Epoch 4/100000
12/12 [==============================] - 0s 20ms/step - loss: 59.8783 - rmse: 44660.4447 - mape: 59.8462 - val_los


Epoch 00030: val_mape improved from 56.56624 to 56.46172, saving model to best_model_neural_network_1024.h5
Epoch 31/100000
12/12 [==============================] - 0s 17ms/step - loss: 55.6202 - rmse: 41933.9931 - mape: 55.6259 - val_loss: 56.6260 - val_rmse: 42613.5664 - val_mape: 56.4781

Epoch 00031: val_mape did not improve from 56.46172
Epoch 32/100000
12/12 [==============================] - 0s 22ms/step - loss: 55.6817 - rmse: 43795.7332 - mape: 55.6064 - val_loss: 56.6204 - val_rmse: 42210.3398 - val_mape: 56.4534

Epoch 00032: val_mape improved from 56.46172 to 56.45343, saving model to best_model_neural_network_1024.h5
Epoch 33/100000
12/12 [==============================] - 0s 17ms/step - loss: 55.2672 - rmse: 42373.0502 - mape: 55.3047 - val_loss: 56.6048 - val_rmse: 41680.3789 - val_mape: 56.4104

Epoch 00033: val_mape improved from 56.45343 to 56.41038, saving model to best_model_neural_network_1024.h5
Epoch 34/100000
12/12 [==============================] - 0s 19ms/ste

12/12 [==============================] - 0s 20ms/step - loss: 34.3877 - rmse: 44082.8353 - mape: 34.3375 - val_loss: 29.9869 - val_rmse: 41560.9453 - val_mape: 29.9774

Epoch 00093: val_mape did not improve from 29.45938
Epoch 94/100000
12/12 [==============================] - 0s 18ms/step - loss: 28.2578 - rmse: 42197.6061 - mape: 28.2712 - val_loss: 29.4073 - val_rmse: 41047.6328 - val_mape: 29.3889

Epoch 00094: val_mape improved from 29.45938 to 29.38893, saving model to best_model_neural_network_1024.h5
Epoch 95/100000
12/12 [==============================] - 0s 19ms/step - loss: 27.8365 - rmse: 40313.4510 - mape: 27.8495 - val_loss: 30.4690 - val_rmse: 41681.0625 - val_mape: 30.4702

Epoch 00095: val_mape did not improve from 29.38893
Epoch 96/100000
12/12 [==============================] - 0s 17ms/step - loss: 28.6801 - rmse: 40641.1508 - mape: 28.7327 - val_loss: 31.0584 - val_rmse: 41818.7656 - val_mape: 31.0614

Epoch 00096: val_mape did not improve from 29.38893
Epoch 97/100


Epoch 00125: val_mape improved from 28.51872 to 28.41116, saving model to best_model_neural_network_1024.h5
Epoch 126/100000
12/12 [==============================] - 0s 39ms/step - loss: 27.0260 - rmse: 40099.7251 - mape: 26.9544 - val_loss: 28.7274 - val_rmse: 41191.6055 - val_mape: 28.7130

Epoch 00126: val_mape did not improve from 28.41116
Epoch 127/100000
12/12 [==============================] - 0s 28ms/step - loss: 27.1959 - rmse: 39930.2816 - mape: 27.1894 - val_loss: 28.6682 - val_rmse: 40648.3594 - val_mape: 28.6377

Epoch 00127: val_mape did not improve from 28.41116
Epoch 128/100000
12/12 [==============================] - 0s 32ms/step - loss: 27.2478 - rmse: 41898.6553 - mape: 27.2055 - val_loss: 30.0765 - val_rmse: 40356.5000 - val_mape: 30.0290

Epoch 00128: val_mape did not improve from 28.41116
Epoch 129/100000
12/12 [==============================] - 0s 30ms/step - loss: 27.7570 - rmse: 38784.6337 - mape: 27.7244 - val_loss: 28.3678 - val_rmse: 40888.3672 - val_mape: 

12/12 [==============================] - 0s 23ms/step - loss: 29.5278 - rmse: 40763.8113 - mape: 29.4911 - val_loss: 31.0353 - val_rmse: 39887.3906 - val_mape: 30.9805

Epoch 00159: val_mape did not improve from 28.00524
Epoch 160/100000
12/12 [==============================] - 0s 24ms/step - loss: 27.9330 - rmse: 40896.4111 - mape: 27.9110 - val_loss: 28.1671 - val_rmse: 40810.4727 - val_mape: 28.1441

Epoch 00160: val_mape did not improve from 28.00524
Epoch 161/100000
12/12 [==============================] - 0s 23ms/step - loss: 26.3669 - rmse: 40871.1647 - mape: 26.3697 - val_loss: 27.8945 - val_rmse: 40510.1797 - val_mape: 27.8562

Epoch 00161: val_mape improved from 28.00524 to 27.85621, saving model to best_model_neural_network_1024.h5
Epoch 162/100000
12/12 [==============================] - 0s 22ms/step - loss: 26.8983 - rmse: 40377.8089 - mape: 26.9082 - val_loss: 28.6491 - val_rmse: 40079.5742 - val_mape: 28.5905

Epoch 00162: val_mape did not improve from 27.85621
Epoch 163

...

12/12 [==============================] - 0s 18ms/step - loss: 19.3742 - rmse: 34789.2118 - mape: 19.4003 - val_loss: 21.3851 - val_rmse: 35171.2891 - val_mape: 21.3320

Epoch 18993: val_mape did not improve from 17.58817
Epoch 18994/100000
12/12 [==============================] - 0s 18ms/step - loss: 19.3951 - rmse: 33934.7889 - mape: 19.3795 - val_loss: 21.6829 - val_rmse: 35272.8281 - val_mape: 21.6309

Epoch 18994: val_mape did not improve from 17.58817
Epoch 18995/100000
12/12 [==============================] - 0s 18ms/step - loss: 19.3800 - rmse: 34031.3224 - mape: 19.3815 - val_loss: 21.7516 - val_rmse: 35237.1172 - val_mape: 21.7011

Epoch 18995: val_mape did not improve from 17.58817
Epoch 18996/100000
12/12 [==============================] - 0s 18ms/step - loss: 19.4300 - rmse: 35728.4718 - mape: 19.4310 - val_loss: 21.7983 - val_rmse: 35583.6836 - val_mape: 21.7389

Epoch 18996: val_mape did not improve from 17.58817
Epoch 18997/100000
12/12 [==============================] -

12/12 [==============================] - 0s 20ms/step - loss: 19.6489 - rmse: 34527.4733 - mape: 19.6215 - val_loss: 21.8625 - val_rmse: 35215.7852 - val_mape: 21.8089

Epoch 19061: val_mape did not improve from 17.58817
Epoch 19062/100000
12/12 [==============================] - 0s 20ms/step - loss: 19.2927 - rmse: 35749.3756 - mape: 19.2995 - val_loss: 21.6106 - val_rmse: 35228.8867 - val_mape: 21.5625

Epoch 19062: val_mape did not improve from 17.58817
Epoch 19063/100000
12/12 [==============================] - 0s 20ms/step - loss: 19.1301 - rmse: 34385.3029 - mape: 19.1034 - val_loss: 21.5038 - val_rmse: 35145.2148 - val_mape: 21.4344

Epoch 19063: val_mape did not improve from 17.58817
Epoch 19064/100000
12/12 [==============================] - 0s 22ms/step - loss: 19.6458 - rmse: 35575.3395 - mape: 19.6392 - val_loss: 21.4127 - val_rmse: 35065.3203 - val_mape: 21.3529

Epoch 19064: val_mape did not improve from 17.58817
Epoch 19065/100000
12/12 [==============================] -

12/12 [==============================] - 0s 19ms/step - loss: 19.3405 - rmse: 34993.3984 - mape: 19.3291 - val_loss: 21.1795 - val_rmse: 34950.1367 - val_mape: 21.1365

Epoch 19129: val_mape did not improve from 17.58817
Epoch 19130/100000
12/12 [==============================] - 0s 21ms/step - loss: 19.3496 - rmse: 34484.4384 - mape: 19.3743 - val_loss: 21.4785 - val_rmse: 34754.7852 - val_mape: 21.4183

Epoch 19130: val_mape did not improve from 17.58817
Epoch 19131/100000
12/12 [==============================] - 0s 20ms/step - loss: 18.8981 - rmse: 34604.6188 - mape: 18.8781 - val_loss: 21.4913 - val_rmse: 34721.3867 - val_mape: 21.4418

Epoch 19131: val_mape did not improve from 17.58817
Epoch 19132/100000
12/12 [==============================] - 0s 21ms/step - loss: 19.0950 - rmse: 35667.9144 - mape: 19.1110 - val_loss: 21.4588 - val_rmse: 34637.6680 - val_mape: 21.3991

Epoch 19132: val_mape did not improve from 17.58817
Epoch 19133/100000
12/12 [==============================] -

12/12 [==============================] - 0s 19ms/step - loss: 19.3224 - rmse: 34453.5255 - mape: 19.3097 - val_loss: 21.6657 - val_rmse: 35070.6719 - val_mape: 21.6181

Epoch 19197: val_mape did not improve from 17.58817
Epoch 19198/100000
12/12 [==============================] - 0s 18ms/step - loss: 19.3596 - rmse: 36320.4937 - mape: 19.3312 - val_loss: 21.2882 - val_rmse: 35046.2500 - val_mape: 21.2321

Epoch 19198: val_mape did not improve from 17.58817
Epoch 19199/100000
12/12 [==============================] - 0s 19ms/step - loss: 19.0969 - rmse: 34720.4606 - mape: 19.1028 - val_loss: 21.4557 - val_rmse: 35016.5469 - val_mape: 21.4144

Epoch 19199: val_mape did not improve from 17.58817
Epoch 19200/100000
12/12 [==============================] - 0s 20ms/step - loss: 19.4413 - rmse: 35938.2476 - mape: 19.4350 - val_loss: 22.1598 - val_rmse: 35335.6055 - val_mape: 22.1132

Epoch 19200: val_mape did not improve from 17.58817
Epoch 19201/100000
12/12 [==============================] -

12/12 [==============================] - 0s 21ms/step - loss: 19.0618 - rmse: 36041.4895 - mape: 19.0553 - val_loss: 21.5599 - val_rmse: 35529.3750 - val_mape: 21.4767

Epoch 19265: val_mape did not improve from 17.58817
Epoch 19266/100000
12/12 [==============================] - 0s 21ms/step - loss: 18.9412 - rmse: 34153.0499 - mape: 18.9759 - val_loss: 21.2892 - val_rmse: 35616.6523 - val_mape: 21.2275

Epoch 19266: val_mape did not improve from 17.58817
Epoch 19267/100000
12/12 [==============================] - 0s 21ms/step - loss: 18.9338 - rmse: 34117.8579 - mape: 18.9260 - val_loss: 21.2770 - val_rmse: 35532.1523 - val_mape: 21.2032

Epoch 19267: val_mape did not improve from 17.58817
Epoch 19268/100000
12/12 [==============================] - 0s 22ms/step - loss: 18.6276 - rmse: 34509.2758 - mape: 18.5956 - val_loss: 21.2596 - val_rmse: 35559.2773 - val_mape: 21.1937

Epoch 19268: val_mape did not improve from 17.58817
Epoch 19269/100000
12/12 [==============================] -

In [617]:
mean_absolute_percentage_error(y_test,NN_model.predict(X_test))

0.16650859510460472

In [636]:
model_NN = load_model(f'best_model_neural_network_{batch_size}.h5',compile=False)
# model_NN = load_model(f'best_model_neural_network_with_customer_{batch_size}.h5',compile=False)
# model_NN = load_model(f'best_model_neural_network_del_outlier_{batch_size}.h5',compile=False)
# model_NN = load_model(f'best_model_neural_network_del_outlier_with_customer_{batch_size}.h5',compile=False)

In [637]:
mean_absolute_percentage_error(y_test,model_NN.predict(X_test))

0.3712102691182021

In [384]:
model_NN.predict(np.asarray([le_name.transform(['エンジン'])[0],
                             le_model.transform(['J111G'])[0],
                             le_engine.transform(['EF-DEM'])[0],
#                              le_customer.transform(['FADEEV EVGENY'])[0],
                             5,
                             2015]).reshape(1,-1))

array([[75057.66]], dtype=float32)

# Using Machine Learning

In [257]:
rmse = []
mape = []
r_squared = []
for  model in models:
    model.fit(X_train, y_train)
    y_pred  = model.predict(X_test)
    rmse_score = mean_squared_error(y_test, y_pred,squared=False)
    mape_score = np.mean(np.abs((y_test.values - y_pred)/y_test.values)*100)
    print(mape_score)
    r_squared_score  = model.score(X_test,y_test)
    r_squared.append(r_squared_score)
    rmse.append(rmse_score)
    mape.append(mape_score)

19.875820809894766
21.58015718471826
11.466020413799368
11.491199322784542
13.385108567634655


In [258]:
df_score = pd.DataFrame()
df_score['MODELS'] = names
df_score['R_SQUARED'] = r_squared
df_score['RMSE'] = rmse
df_score['MAPE'] = mape
df_score['RMSE'] = round(df_score['RMSE'],3)
df_score['MAPE'] = round(df_score['MAPE'],3)
df_score['R_SQUARED'] = round(df_score['R_SQUARED'],3)

df_score

MODELS  R_SQUARED      RMSE    MAPE
0  Gradient_Boosting      0.727  7089.558  19.876
1      Decision_Tree      0.637  8181.576  21.580
2        Extra_Trees      0.862  5045.438  11.466
3      Random_Forest      0.870  4903.691  11.491
4            XGBoost      0.870  4890.363  13.385

# Using ExtraTrees Regressor

In [316]:
model_tree = ExtraTreesRegressor()
model_tree.fit(X_train,y_train)

ExtraTreesRegressor()

In [317]:
X_train

Tên phụ tùng_商品名  Model xe_車輌型式  Engine model_エンジン型式  \
14705                 0            453                  216   
14473                 0             59                  141   
6459                  0           1076                  267   
14303                 0            641                   10   
4707                  0            951                  260   
...                 ...            ...                  ...   
11285                 0             98                  249   
11965                 1            844                   21   
5390                  1           1162                  260   
860                   0             34                  211   
15797                 0            626                   10   

       Tháng bán hàng_売上月  Năm bán hàng_売上年  
14705                   5              2013  
14473                   5              2013  
6459                    5              2020  
14303                   4              2013  
4707                    3              2017  
...                   ...               ...  
11285                  11              2016  
11965                   3              2019  
5390                    7              2017  
860                     4              2015  
15797                  11              2013  

[12639 rows x 5 columns]

In [318]:
le_name.classes_

array(['エンジン', 'ノーズカット（個別）', 'フェイスカット', 'フロントアクスル（個別）', 'ミッション（個別）',
       'リアアクスル（個別）', 'リアホーシング（デフ無）（個別）', '外装コンプリート', 'ＣＫＤ／コンプリート',
       'ＣＫＤ／コンプリート（バイヤー）', 'Ｆアクスル（生/Ｄ）', 'Ｒアクスル（生/Ｄ）'], dtype=object)

In [334]:
model.predict(np.array([le_name.transform(['エンジン']),le_model.transform(['AT211']),le_engine.transform(['7A-FE']),7,2015]).reshape(1,-1))

array([32527.82], dtype=float32)

In [263]:
np.array([le_name.transform(['エンジン']),le_model.transform(['AT211']),le_engine.transform(['7A-FE']),12,2021]).reshape(1,-11).shape

(1, 5)

In [330]:
model_linear = LinearRegression()

In [331]:
model_linear.fit(X_train,y_train)
mean_absolute_percentage_error(y_test,model_linear.predict(X_test))

0.53770280510957

In [333]:
model_linear.predict(np.array([le_name.transform(['エンジン']),le_model.transform(['AT211']),le_engine.transform(['7A-FE']),7,2015]).reshape(1,-1))

array([26177.88898275])

# Super Learning